- Collects uniprot features
- NSEuronet, ClinVar, gnomAD datasets (missense variants)
- REVEL & BayesDelx2 datasets
- Genomic coordinates <--> protein position functions
- df for stat score analysis

In [1]:
import pandas as pd
import os
#from Bio import SeqIO
#from io import StringIO
import requests
import time
import json
import re 

import seaborn as sns

In [4]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', 20)
pd.set_option('display.max_rows', None) 

In [2]:
# Set gene
gene = 'PTPN11'

# Dictionary of Uniprot IDs for each gene
uniprot_ids = {
    "PTPN11": "Q06124",    
}

#### Processing functions

In [21]:
# Universal tools for dealing with proteins

aaconv = {'CYS': 'C', 'ASP': 'D', 'SER': 'S', 'GLN': 'Q', 'LYS': 'K',
     'ILE': 'I', 'PRO': 'P', 'THR': 'T', 'PHE': 'F', 'ASN': 'N', 
     'GLY': 'G', 'HIS': 'H', 'LEU': 'L', 'ARG': 'R', 'TRP': 'W', 
     'ALA': 'A', 'VAL':'V', 'GLU': 'E', 'TYR': 'Y', 'MET': 'M',
     'H1S': 'H', 'H2S': 'H'}

aacharge = {
         'C': 0, 'D': -1, 'S': 0, 'Q': 0, 'K': 1,
         'I': 0, 'P': 0, 'T': 0, 'F': 0, 'N': 0, 
         'G': 0, 'H': 0, 'L': 0, 'R': 1, 'W': 0, 
         'A': 0, 'V':0, 'E': -1, 'Y': 0, 'M': 0 }

aachargeHP = {
         'C': 0, 'D': -1, 'S': 0, 'Q': 0, 'K': 1,
         'I': 0, 'P': 0, 'T': 0, 'F': 0, 'N': 0, 
         'G': 0, 'H': 1, 'L': 0, 'R': 1, 'W': 0, 
         'A': 0, 'V':0, 'E': -1, 'Y': 0, 'M': 0 }

In [ ]:
"""

# Functions to test tables processing for any unexpected results

def threetoone(x):
    if len(x) % 3 != 0: 
        raise ValueError('Input length should be a multiple of three')

    y = ''
    for i in range(len(x) // 3):
            y += aaconv[x[3 * i : 3 * i + 3]]
    return y

def testTable(table,mutation="Protein_desc",threeLetter=False):
    mutation = table[mutation].apply(lambda x: str(x).split(".")[-1] if pd.notna(x) else "")
    locations=mutation.apply(lambda x: int(re.findall('\d+', x)[0]))
    if threeLetter:
        fromAA = mutation.apply(lambda x: aaconv[re.split('\d+',x)[0].upper()])
        toAA = mutation.apply(lambda x: aaconv[re.split('\d+',x)[1].upper()])
    else:
        fromAA = mutation.apply(lambda x: re.findall('[A-Z]+', x.upper())[0])
        toAA = mutation.apply(lambda x: re.findall('[A-Z]+', x.upper())[1])
    problem_idx = set()
    problem_idx.update(locations[locations > protein_length].index.tolist())
    problem_idx.update(fromAA[~fromAA.isin(aacharge.keys())].index.tolist())
    problem_idx.update(toAA[~toAA.isin(aacharge.keys())].index.tolist())

    return problem_idx

"""

In [17]:
# Function to filter table for missense mutations
def filterTable_missense(df, gene, mutation_col="Protein_desc", gene_col="Gene", threeLetter=False):

    # Handle gene column logic
    if gene_col in df.columns:
        df = df.loc[df[gene_col].astype(str).str.contains(gene, na=False)]
    else:
        df.loc[:, gene_col] = gene
        
    # Safe extraction of protein change
    mutation = df[mutation_col].apply(lambda x: str(x).split(".")[-1] if pd.notna(x) else "")

    # Extract positions (integer)
    locations = mutation.apply(lambda x: int(re.findall(r'\d+', x)[0]) if re.findall(r'\d+', x) else -1)

    # Extract AA from/to
    if threeLetter:
        fromAA = mutation.apply(lambda x: aaconv[re.split(r'\d+', x)[0].upper()] if re.split(r'\d+', x)[0].upper() in aaconv else "")
        toAA   = mutation.apply(lambda x: aaconv[re.split(r'\d+', x)[1].upper()] if len(re.split(r'\d+', x)) > 1 and re.split(r'\d+', x)[1].upper() in aaconv else "")
    else:
        fromAA = mutation.apply(lambda x: re.findall(r'[A-Z]+', x.upper())[0] if re.findall(r'[A-Z]+', x.upper()) else "")
        toAA   = mutation.apply(lambda x: re.findall(r'[A-Z]+', x.upper())[1] if len(re.findall(r'[A-Z]+', x.upper())) > 1 else "")

    # Identify problematic rows
    problem_idx = set()
    problem_idx.update(locations[locations > protein_length].index.tolist())
    problem_idx.update(fromAA[~fromAA.isin(aacharge.keys())].index.tolist())
    problem_idx.update(toAA[~toAA.isin(aacharge.keys())].index.tolist())
    problem_idx.update(df.index[fromAA == toAA]) # to check no synonomous variants in form A1A

    missense_df = df.drop(index=problem_idx, errors='ignore')

    # Report mismatched rows
    notmissense_df = df.loc[df.index.isin(problem_idx)]
    #check_notmissense_rows = notmissense_df.loc[notmissense_df[mutation_col].notna()]

    """
    if verbose:
        print(notmissense_df)
    else:
        check_notmissense_rows = notmissense_df.loc[notmissense_df[mutation_col].notna()]
        print(check_notmissense_rows)"""
    
    return missense_df, notmissense_df #, check_notmissense_rows


In [18]:
# Function to extend tables

def extendTableProtein(table,mutation="Protein_desc",threeLetter=False, DCharge=False):
    table["Protein_change"] = table[mutation].astype(str).apply(lambda x: x.split(".")[-1])
    table["AApos"] = table["Protein_change"].apply(lambda x:int( re.findall('\d+', x)[0])) # extract amino acid position
    if threeLetter:
        table["Protein_change"] = table["Protein_change"].str.upper()
        table["AAfrom"] = table["Protein_change"].apply(lambda x: aaconv[re.split('\d+',x)[0].upper()])
        table["AAto"] = table["Protein_change"].apply(lambda x: aaconv[re.split('\d+',x)[1].upper()])
        table["Protein_change"] = table["AAfrom"] + table["AApos"].astype(str) + table["AAto"]
    else:
        table["AAfrom"] = table["Protein_change"].apply(lambda x: re.findall('[A-Z]+', x.upper())[0])
        table["AAto"] = table["Protein_change"].apply(lambda x: re.findall('[A-Z]+', x.upper())[1])
    if DCharge:
        table["DCharge"] = table["Protein_change"].apply(lambda x: aacharge[re.findall('[A-Z]+', x.upper())[1]] - aacharge[re.findall('[A-Z]+', x.upper())[0]]) 
        table["DChargeHP"] = table["Protein_change"].apply(lambda x: aachargeHP[re.findall('[A-Z]+', x.upper())[1]] - aachargeHP[re.findall('[A-Z]+', x.upper())[0]]) 
    return table

def extendTableDNA(table,mutation="cDNA"):
    table["chr"] = chrom # extracted from ClinVar
    table["codon"] = table[mutation].apply(lambda x: re.sub("\D+","",x))
    table["ref"] = table[mutation].apply(lambda x: re.split("\d",re.split('>',x)[0])[-1])
    table["alt"] = table[mutation].apply(lambda x: re.split('>',x)[-1])
    return table

### Read in data

#### Uniprot

In [10]:
# Fetch sequence length, domains and sites from UniProt

def get_uniprot_features(gene):
    uniprot_id = uniprot_ids[gene]
    url = f"https://rest.uniprot.org/uniprotkb/{uniprot_id}.json"
    response = requests.get(url)
    response.raise_for_status()
    data = response.json()

    sequence_length = len(data['sequence']['value'])
    
    domains_list = []
    sites_list = []
    other_features = []
    
    # Assign colors for each feature type
    feature_colours = {
        'Domain': "#66c2a5",
        'Region': "#fc8d62",
        'Active site': "#e78ac3",
        'Binding site': "#a6d854"
    }
    
    for feature in data.get('features', []):
        ftype = feature['type']
        start = feature['location']['start']['value']
        end = feature['location']['end']['value']
        name = feature.get('description', ftype)
        
        # Collect domains
        if ftype in ['Domain', 'Region']:
            domains_list.append([name, start, end, feature_colours[ftype]])
        # Collect sites
        elif ftype in ['Active site', 'Binding site']:
            sites_list.append([name, start, end, feature_colours[ftype]])
        
        else:
            other_features.append({
                "type": ftype,
                "name": name,
                "start": start,
                "end": end
            })

    """
    # Assign distinct colors for domains
    palette = sns.color_palette("Set2", n_colors=len(domains_list))
    for i, domain in enumerate(domains_list):
        domain[3] = palette[i]
    """
    
    return sequence_length, domains_list, sites_list, other_features

In [19]:
protein_length, domains, sites, others = get_uniprot_features(gene)

print("Gene:", gene)

print("Sequence Length:", protein_length)

print("Domains / regions:")
for domain in domains:
    print (domain)

print("\nActive / binding sites:")
for site in sites:
    print (site)

print("\nOther features:")
for other in others:
    print (other)

# Save features dictionaries
uniprot_features = {
    "domains": domains,
    "sites": sites,
    "other features": others
}

with open(f"{gene}_uniprotfeatures.json", "w") as f:
    json.dump(uniprot_features, f, indent=2)

Gene: PTPN11
Sequence Length: 593
Domains / regions:
['SH2 1', 6, 102, '#66c2a5']
['SH2 2', 112, 216, '#66c2a5']
['Tyrosine-protein phosphatase', 247, 517, '#66c2a5']
['Disordered', 548, 571, '#fc8d62']

Active / binding sites:
['Phosphocysteine intermediate', 459, 459, '#e78ac3']
['', 425, 425, '#a6d854']
['', 459, 465, '#a6d854']
['', 506, 506, '#a6d854']

Other features:
{'type': 'Initiator methionine', 'name': 'Removed', 'start': 1, 'end': 1}
{'type': 'Chain', 'name': 'Tyrosine-protein phosphatase non-receptor type 11', 'start': 2, 'end': 593}
{'type': 'Compositional bias', 'name': 'Pro residues', 'start': 559, 'end': 568}
{'type': 'Modified residue', 'name': 'N-acetylthreonine', 'start': 2, 'end': 2}
{'type': 'Modified residue', 'name': 'Phosphotyrosine', 'start': 62, 'end': 62}
{'type': 'Modified residue', 'name': 'Phosphotyrosine', 'start': 66, 'end': 66}
{'type': 'Modified residue', 'name': 'Phosphotyrosine; by PDGFR', 'start': 542, 'end': 542}
{'type': 'Modified residue', 'nam

#### NSEuronet

In [141]:
# Manually load the NSEuronetData.csv (for all RAS genes)

df1 = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\NSEuroNetData.csv", sep=';', header=None)
df1_headers = ["Gene", "cDNA", "Protein_desc", "Disease"] #headers to add to df
df1.columns = df1_headers

print(df1.head())

     Gene       cDNA Protein_desc          Disease
0    KRAS    c.65A>G       p.Q22R  Noonan syndrome
1  PTPN11   c.922A>G      p.N308D  Noonan syndrome
2  PTPN11   c.184T>G       p.Y62D  Noonan syndrome
3  PTPN11   c.922A>G      p.N308D  Noonan syndrome
4  PTPN11  c.1232C>T      p.T411M  Noonan syndrome


In [142]:
# Filter NSEuronet df for missense variants
df1_missense, df1_notmissense = filterTable_missense(df1, gene, mutation_col="Protein_desc", gene_col="Gene", threeLetter=False)


In [143]:
# Extend NSEuronet df to create Protein_change, AA and charge columns
NSEuronet_df = extendTableProtein(df1_missense,mutation="Protein_desc",threeLetter=False,DCharge=True)
NSEuronet_df

Gene                 cDNA      Protein_desc              Disease  \
1     PTPN11             c.922A>G           p.N308D      Noonan syndrome   
2     PTPN11             c.184T>G            p.Y62D      Noonan syndrome   
3     PTPN11             c.922A>G           p.N308D      Noonan syndrome   
4     PTPN11            c.1232C>T           p.T411M      Noonan syndrome   
5     PTPN11            c.1232C>T           p.T411M      Noonan syndrome   
6     PTPN11            c.1232C>T           p.T411M      Noonan syndrome   
7     PTPN11            c.1529A>G           p.Q510R  NF1-Noonan syndrome   
8     PTPN11             c.179G>C            p.G60A      Noonan syndrome   
9     PTPN11             c.182A>G            p.D61G      Noonan syndrome   
10    PTPN11             c.184T>G            p.Y62D      Noonan syndrome   
11    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
12    PTPN11             c.218C>T            p.T73I      Noonan syndrome   
13    PTPN11             c.236A>G            p.Q79R      Noonan syndrome   
14    PTPN11             c.236A>G            p.Q79R      Noonan syndrome   
15    PTPN11             c.236A>G            p.Q79R      Noonan syndrome   
16    PTPN11             c.317A>C           p.D106A      Noonan syndrome   
17    PTPN11             c.417G>C           p.E139D      Noonan syndrome   
18    PTPN11             c.417G>C           p.E139D      Noonan syndrome   
19    PTPN11             c.854T>C           p.F285S      Noonan syndrome   
20    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
21    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
22    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
23    PTPN11            c.1472C>A           p.P491H      Noonan syndrome   
24    PTPN11            c.1471C>T           p.P491S      Noonan syndrome   
25    PTPN11            c.1510A>G           p.M504V      Noonan syndrome   
26    PTPN11            c.1505C>T           p.S502L      Noonan syndrome   
27    PTPN11             c.836A>G           p.Y279C  LEOPARD syndrome...   
28    PTPN11            c.1472C>T           p.P491L      Noonan syndrome   
29    PTPN11            c.1472C>T           p.P491L      Noonan syndrome   
30    PTPN11            c.1472C>T           p.P491L      Noonan syndrome   
31    PTPN11             c.766C>A           p.Q256K      Noonan syndrome   
32    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
33    PTPN11             c.218C>T            p.T73I      Noonan syndrome   
34    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
35    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
36    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
37    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
38    PTPN11             c.218C>T            p.T73I      Noonan syndrome   
39    PTPN11             c.172A>G            p.N58D      Noonan syndrome   
40    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
41    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
42    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
43    PTPN11             c.206A>T            p.E69V      Noonan syndrome   
44    PTPN11             c.836A>G           p.Y279C      Noonan syndrome   
45    PTPN11             c.844A>G           p.I282V      Noonan syndrome   
46    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
47    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
48    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
49    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
50    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
51    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
52    PTPN11             c.922A>G           p.N308D     

#### ClinVar

NCBI E-utilities rate is limited to 3 requests per second (without an API key). Can request an NCBI API key to increase limit to ~10 per second.

Try again teXML release (gzipped) and parse for gene of interest

ClinVar maintains a complete set of variant data on an FTP server. Weekly update cycle but only the realease on the 1st Thursday of the month is archived. Download this below. https://pmc.ncbi.nlm.nih.gov/tools/ftp/

In [30]:
# Manually load the clinvar_result.txt download (for single gene e.g. PTPN11)

df2 = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\clinvar_result.txt", sep="\t", low_memory=False)
print(df2.head())


                  Name              Gene(s) Protein change  \
0  GRCh38/hg38 12p1...  LOC130008261|LOC...            NaN   
1  GRCh38/hg38 12q2...  HECTD4|LOC130008...            NaN   
2  GRCh38/hg38 12q2...  HECTD4|LOC130008...            NaN   
3  GRCh38/hg38 12q2...          PTPN11|RPL6            NaN   
4  NM_002834.3(PTPN...          PTPN11|RPL6            NaN   

          Condition(s)     Accession  GRCh37Chromosome       GRCh37Location  \
0            See cases  VCV000150740              12.0   282465 - 133773393   
1            See cases  VCV000059818              12.0  112741234 - 1131...   
2            See cases  VCV000059819              12.0  112745336 - 1131...   
3            See cases  VCV000145960              12.0  112854667 - 1128...   
4  Noonan syndrome ...  VCV000882155              12.0            112856599   

   GRCh38Chromosome       GRCh38Location  VariationID  AlleleID(s)  \
0              12.0   121271 - 133196807       150740       160491   
1           

In [31]:
# Filter ClinVar df for missense variants

# But first extract Protein_desc from 'Name' column
df2['Protein_desc'] = (df2['Name'].str.extract(r'(p\.[A-Za-z0-9]+)').iloc[:, 0].str.replace(')', '', regex=False).str.strip())
df2['cDNA_desc'] = df2['Name'].str.extract(r'(c\.[0-9]+[ACGT]>[ACGT])')[0]


with pd.option_context('display.max_colwidth', 15):
    df2_missense, df2_notmissense = filterTable_missense(df2, gene, mutation_col="Protein_desc",  gene_col="Gene(s)", threeLetter=True)


In [ ]:
print(df2["Molecular consequence"].unique())


In [ ]:
with pd.option_context('display.max_colwidth', None):
    print(df2_missense.head())
    #print(df2_missense[df2_missense["Molecular consequence"].str.lower() != "missense variant"])


In [32]:
# Extend ClinVar df to create Protein_change, AA and charge columns
ClinVar_df = extendTableProtein(df2_missense,mutation="Protein_desc",threeLetter=True,DCharge=True)
ClinVar_df

Name Gene(s)       Protein change         Condition(s)  \
24    NM_002834.5(PTPN...  PTPN11                  M1R  Juvenile myelomo...   
25    NM_002834.5(PTPN...  PTPN11                  T2I  LEOPARD syndrome...   
30    NM_002834.5(PTPN...  PTPN11                  R4G         not provided   
31    NM_002834.5(PTPN...  PTPN11                  R4Q            RASopathy   
58    NM_002834.5(PTPN...  PTPN11                  W6C  Cardiovascular p...   
59    NM_002834.5(PTPN...  PTPN11                  W6C  Cardiovascular p...   
60    NM_002834.5(PTPN...  PTPN11                 N10Y  not provided|Car...   
61    NM_002834.5(PTPN...  PTPN11                 N10H   Metachondromatosis   
62    NM_002834.5(PTPN...  PTPN11                 N10D  Cardiovascular p...   
63    NM_002834.5(PTPN...  PTPN11                 N10T  RASopathy|not pr...   
64    NM_002834.5(PTPN...  PTPN11                 N10S  not provided|RAS...   
65    NM_002834.5(PTPN...  PTPN11                 I11T            RASopathy   
66    NM_002834.5(PTPN...  PTPN11                 T12A            RASopathy   
69    NM_002834.5(PTPN...  PTPN11                 V14L         not provided   
72    NM_002834.5(PTPN...  PTPN11                 N18D  Cardiovascular p...   
73    NM_002834.5(PTPN...  PTPN11                 N18S            RASopathy   
75    NM_002834.5(PTPN...  PTPN11                 L19V            RASopathy   
77    NM_002834.5(PTPN...  PTPN11                 T22A  Juvenile myelomo...   
79    NM_002834.5(PTPN...  PTPN11                 G24A  Cardiovascular p...   
80    NM_002834.5(PTPN...  PTPN11                 G27D         not provided   
81    NM_002834.5(PTPN...  PTPN11                 A31S         not provided   
82    NM_002834.5(PTPN...  PTPN11                 A31G   LEOPARD syndrome 1   
86    NM_002834.5(PTPN...  PTPN11                 K35E            RASopathy   
87    NM_002834.5(PTPN...  PTPN11                 K35Q  Cardiovascular p...   
88    NM_002834.5(PTPN...  PTPN11                 K35I            RASopathy   
91    NM_002834.5(PTPN...  PTPN11                 G39R  RASopathy|not pr...   
93    NM_002834.5(PTPN...  PTPN11                 D40G        not specified   
95    NM_002834.5(PTPN...  PTPN11                 T42S         not provided   
96    NM_002834.5(PTPN...  PTPN11                 T42A  Noonan syndrome ...   
98    NM_002834.5(PTPN...  PTPN11                 L43V  RASopathy|LEOPAR...   
99    NM_002834.5(PTPN...  PTPN11                 L43F  RASopathy|Cardio...   
102   NM_002834.5(PTPN...  PTPN11                 V45I            RASopathy   
114   NM_002834.5(PTPN...  PTPN11           G48R, G49R  not provided|Ewi...   
115   NM_002834.5(PTPN...  PTPN11           A50T, A49T            RASopathy   
116   NM_002834.5(PTPN...  PTPN11           T51N, T52N            RASopathy   
117   NM_002834.5(PTPN...  PTPN11           T52I, T51I            RASopathy   
121   NM_002834.5(PTPN...  PTPN11           K55R, K54R            RASopathy   
122   NM_002834.5(PTPN...  PTPN11           I56V, I55V  Noonan syndrome ...   
123   NM_002834.5(PTPN...  PTPN11           I56T, I55T  Noonan syndrome ...   
126   NM_002834.5(PTPN...  PTPN11           Q56H, Q57H      Noonan syndrome   
129   NM_002834.5(PTPN...  PTPN11           N58Y, N57Y  not provided|RAS...   
130   NM_002834.5(PTPN...  PTPN11           N58D, N57D  Male infertility...   
131   NM_002834.5(PTPN...  PTPN11           N58H, N57H  not provided|RAS...   
132   NM_002834.5(PTPN...  PTPN11           N58S, N57S  Noonan syndrome ...   
133   NM_002834.5(PTPN...  PTPN11           N58K, N57K  Noonan syndrome|...   
134   NM_002834.5(PTPN...  PTPN11           N58K, N57K  Noonan syndrome ...   
135   NM_002834.5(PTPN...  PTPN11           T59A, T58A  not provided|PTP...   
137   NM_002834.5(PTPN...  PTPN11           G60R, G59R  not provided|RAS...   
138   NM_002834.5(PTPN...  PTPN11           G60C, G59C  Cardiovascular p...   
139   NM_002834.5(PTPN...  PTPN11           G60S, G59S  PTPN11-related 

In [46]:
print(ClinVar_df[ClinVar_df['Germline classification'].str.contains('enign')])

                     Name Gene(s)       Protein change         Condition(s)  \
73    NM_002834.5(PTPN...  PTPN11                 N18S            RASopathy   
280   NM_002834.5(PTPN...  PTPN11         K131R, K130R            RASopathy   
623   NM_002834.5(PTPN...  PTPN11         I309V, I308V            RASopathy   
626   NM_002834.5(PTPN...  PTPN11         M310T, M311T            RASopathy   
678   NM_002834.5(PTPN...  PTPN11         R343Q, R342Q            RASopathy   
690   NM_002834.5(PTPN...  PTPN11         R351Q, R350Q            RASopathy   
874   NM_002834.5(PTPN...  PTPN11  T467S, T468S, T472S      Noonan syndrome   
886   NM_002834.5(PTPN...  PTPN11  I473V, I474V, I478V    Noonan syndrome 1   
1053  NM_002834.5(PTPN...  PTPN11  T553M, T557M, T552M            RASopathy   
1069  NM_002834.5(PTPN...  PTPN11  L560F, L564F, L559F            RASopathy   
1116  NM_002834.5(PTPN...  PTPN11  L584M, L589M, L585M  Cardiovascular p...   

         Accession  GRCh37Chromosome GRCh37Location

#### gnomAD

In [14]:
df3 = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\gnomAD_v4.1.0_ENSG00000179295_2025_11_07_16_02_00.csv")

In [61]:
df3.head()

gnomAD ID  Chromosome   Position         rsIDs Reference  \
0    12-112419037-C-T          12  112419037           NaN         C   
1    12-112419039-G-A          12  112419039           NaN         G   
2  12-112419039-G-GGT          12  112419039  rs2037471954         G   
3    12-112419041-C-T          12  112419041  rs1463949594         C   
4    12-112419042-C-T          12  112419042           NaN         C   

  Alternate               Source Filters - exomes Filters - genomes  \
0         T        gnomAD Exomes             PASS               NaN   
1         A        gnomAD Exomes             PASS               NaN   
2       GGT  gnomAD Exomes,gn...             PASS              PASS   
3         T  gnomAD Exomes,gn...             PASS              PASS   
4         T        gnomAD Exomes             PASS               NaN   

          Transcript HGVS Consequence Protein Consequence  \
0  ENST00000351677.7         c.-75C>T                 NaN   
1  ENST00000351677.7         c.-73G>A                 NaN   
2  ENST00000351677.7   c.-73_-72insGT                 NaN   
3  ENST00000351677.7         c.-71C>T                 NaN   
4  ENST00000351677.7         c.-70C>T                 NaN   

  Transcript Consequence       VEP Annotation ClinVar Germline Classification  \
0             c.-75C>T    5_prime_UTR_variant                  NaN              
1             c.-73G>A    5_prime_UTR_variant                  NaN              
2       c.-73_-72insGT    5_prime_UTR_variant                  NaN              
3             c.-71C>T    5_prime_UTR_variant  Uncertain signif...              
4             c.-70C>T    5_prime_UTR_variant                  NaN              

   ClinVar Variation ID Flags  Allele Count  Allele Number  Allele Frequency  \
0                  NaN    NaN             1        1525952      6.553286e-07   
1                  NaN    NaN             1        1530186      6.535153e-07   
2                  NaN    NaN             2        1530078      1.307123e-06   
3             882209.0    NaN            24        1531396      1.567198e-05   
4                  NaN    NaN             1        1531496      6.529563e-07   

   Homozygote Count  Hemizygote Count Filters - joint GroupMax FAF group  \
0                 0                 0            PASS                NaN   
1                 0                 0            PASS                NaN   
2                 0                 0            PASS                eas   
3                 0                 0            PASS                nfe   
4                 0                 0            PASS                NaN   

   GroupMax FAF frequency  cadd  revel_max  spliceai_ds_max  \
0                  NaN     20.6        NaN              0.0   
1                  NaN     20.7        NaN              0.0   
2             0.000008     20.4        NaN              0.0   
3             0.000013     21.1        NaN              0.0   
4                  NaN     20.5        NaN              0.0   

   pangolin_largest_ds  phylop  sift_max  polyphen_max  \
0                 0.01   5.520       NaN           NaN   
1                 0.01   4.560       NaN           NaN   
2                 0.08   4.560       NaN           NaN   
3                 0.01   4.570       NaN           NaN   
4                -0.04   0.995       NaN           NaN   

   Allele Count African/African American  \
0                    0                     
1                    0                     
2                    0                     
3                    0                     
4                    0                     

   Allele Number African/African American  \
0                71260                      
1                71576                      
2                71458                      
3                71484                      
4                71606                      

   Homozygote Count African/African American  \
0                    0                         


In [15]:
len(df3)

2189

In [22]:
df3_missense, df3_notmissense = filterTable_missense(df3, gene, mutation_col="Protein Consequence", threeLetter=True)


In [25]:
gnomAD_df = extendTableProtein(df3_missense,mutation="Protein Consequence",threeLetter=True,DCharge=True)

In [26]:
gnomAD_df

gnomAD ID  Chromosome   Position         rsIDs Reference  \
54    12-112419116-C-T          12  112419116   rs267606990         C   
58    12-112419121-C-G          12  112419121   rs886041517         C   
59    12-112419122-G-A          12  112419122           NaN         G   
195   12-112446278-G-T          12  112446278           NaN         G   
196   12-112446279-G-T          12  112446279    rs79203122         G   
197   12-112446286-C-T          12  112446286   rs566068139         C   
198   12-112446286-C-G          12  112446286   rs566068139         C   
199   12-112446287-C-G          12  112446287   rs536503257         C   
200   12-112446287-C-A          12  112446287   rs536503257         C   
201   12-112446289-A-G          12  112446289   rs368633510         A   
202   12-112446290-A-G          12  112446290   rs200613531         A   
203   12-112446292-A-G          12  112446292  rs1472357430         A   
204   12-112446293-T-C          12  112446293  rs1181579972         T   
205   12-112446295-A-T          12  112446295           NaN         A   
206   12-112446295-A-G          12  112446295  rs1386827892         A   
211   12-112446313-A-G          12  112446313   rs776089364         A   
212   12-112446314-A-G          12  112446314   rs587778635         A   
213   12-112446315-C-G          12  112446315           NaN         C   
214   12-112446316-C-G          12  112446316  rs2037993841         C   
217   12-112446319-C-G          12  112446319   rs753951666         C   
218   12-112446323-T-G          12  112446323           NaN         T   
220   12-112446325-A-G          12  112446325   rs757537175         A   
221   12-112446325-A-C          12  112446325           NaN         A   
223   12-112446337-G-T          12  112446337   rs750261927         G   
224   12-112446338-A-T          12  112446338  rs1247363600         A   
226   12-112446343-A-G          12  112446343           NaN         A   
227   12-112446344-G-A          12  112446344  rs2135856451         G   
228   12-112446351-G-T          12  112446351           NaN         G   
229   12-112446351-G-C          12  112446351           NaN         G   
232   12-112446362-G-A          12  112446362   rs906966059         G   
233   12-112446364-A-G          12  112446364   rs934388335         A   
234   12-112446364-A-C          12  112446364   rs934388335         A   
235   12-112446365-A-T          12  112446365  rs2037994651         A   
237   12-112446372-C-A          12  112446372  rs1337565783         C   
239   12-112446376-G-C          12  112446376   rs886041585         G   
240   12-112446376-G-A          12  112446376   rs886041585         G   
243   12-112446388-C-G          12  112446388  rs1566164987         C   
247   12-112446394-G-A          12  112446394  rs2037995352         G   
248   12-112446394-G-C          12  112446394  rs2037995352         G   
320   12-112450325-G-C          12  112450325  rs2135861867         G   
321   12-112450325-G-A          12  112450325  rs2135861867         G   
323   12-112450328-G-C          12  112450328   rs587778636         G   
324   12-112450328-G-A          12  112450328   rs587778636         G   
326   12-112450335-C-T          12  112450335   rs397507503         C   
328   12-112450337-C-T          12  112450337  rs2135861929         C   
331   12-112450344-A-G          12  112450344  rs1261667540         A   
333   12-112450346-A-G          12  112450346   rs397507504         A   
335   12-112450353-A-G          12  112450353   rs751437780         A   
336   12-112450355-A-G          12  112450355   rs886043790         A   
337   12-112450358-G-A          12  112450358   rs397507507         G   
338   12-112450359-G-C          12  112450359   rs397507509         G   
339   12-112450359-G-A          12  112450359   rs397507509         G   
340   12-112450361-G-A          12  112450361   rs397507510         G   
341   12-112450362-A-G          12  112450362   rs121918461         A  

In [27]:
len(gnomAD_df)

446

In [47]:
print(gnomAD_df[gnomAD_df['ClinVar Germline Classification'].str.contains('enign', na=False)])

             gnomAD ID  Chromosome   Position         rsIDs Reference  \
212   12-112446314-A-G          12  112446314   rs587778635         A   
516   12-112453254-A-G          12  112453254   rs397516805         A   
1132  12-112477722-A-G          12  112477722   rs201787206         A   
1135  12-112477729-T-C          12  112477729   rs201226824         T   
1238  12-112477951-G-A          12  112477951   rs535800148         G   
1251  12-112477975-G-A          12  112477975   rs397507534         G   
1494  12-112486466-C-G          12  112486466   rs377257792         C   
1639  12-112488483-A-G          12  112488483  rs2135915117         A   
1905  12-112502202-C-T          12  112502202   rs148176616         C   
1918  12-112502222-C-T          12  112502222   rs397516797         C   
2116  12-112504735-C-A          12  112504735           NaN         C   

     Alternate               Source Filters - exomes Filters - genomes  \
212          G  gnomAD Exomes,gn...             P

# ^^ CHROMOSONE 2

#### Meta predictors

## ?? get chromosone range from uniprot but it only has GRCH38 >>

In [20]:
def get_chr_range(df, gene, gene_col="Gene(s)", loc_col="GRCh38Location", chrom_col="GRCh38Chromosome"):
    # Filter for specified gene
    gene_df = df[df[gene_col].astype(str).str.contains(gene, na=False)].copy()

    # Convert location column to numeric (ignore errors)
    gene_df[loc_col] = pd.to_numeric(gene_df[loc_col], errors='coerce')

    # Drop missing positions
    #gene_df = gene_df.dropna(subset=[loc_col])

    # Find chromosome, min, and max positions
    chrom = gene_df[chrom_col].dropna().unique()[0]
    min_pos = gene_df[loc_col].min()
    max_pos = gene_df[loc_col].max()

    print(f" Gene: {gene}")
    print(f" Chromosome: {chrom}")
    print(f" Position range: {int(min_pos)} - {int(max_pos)}")

    return chrom, min_pos, max_pos


##### REVEL

Downloaded from https://sites.google.com/site/revelgenomics/downloads

Try again to curl from dfNSFP

In [16]:
# Manually download the REVEL data (for all genes)

# Read just the first 10 rows (6GB REVEL file)
dfa = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\revel-v1.3_all_chromosomes\revel_with_transcript_ids", nrows=10)
dfa

chr  hg19_pos  grch38_pos ref alt aaref aaalt  REVEL Ensembl_transcriptid
0    1     35142       35142   G   A     T     M  0.027      ENST00000417324
1    1     35142       35142   G   C     T     R  0.035      ENST00000417324
2    1     35142       35142   G   T     T     K  0.043      ENST00000417324
3    1     35143       35143   T   A     T     S  0.018      ENST00000417324
4    1     35143       35143   T   C     T     A  0.034      ENST00000417324
5    1     35143       35143   T   G     T     P  0.039      ENST00000417324
6    1     35144       35144   A   C     C     W  0.012      ENST00000417324
7    1     35145       35145   C   A     C     F  0.023      ENST00000417324
8    1     35145       35145   C   G     C     S  0.029      ENST00000417324
9    1     35145       35145   C   T     C     Y  0.016      ENST00000417324

In [73]:
chrom, min_pos, max_pos = get_chr_range(ClinVar_df, gene, gene_col="Gene(s)", loc_col="GRCh38Location", chrom_col="GRCh38Chromosome")


 Gene: PTPN11
 Chromosome: 12.0
 Position range: 112419113 - 112504754


In [97]:


revel_file = r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\revel-v1.3_all_chromosomes\revel_with_transcript_ids"

chunksize = 1_000_000
ptpn11_revel_chunks = []

for chunk in pd.read_csv(revel_file, chunksize=chunksize, low_memory=False):
    # Convert positions in revel_file to numeric
    chunk['grch38_pos'] = pd.to_numeric(chunk['grch38_pos'], errors='coerce')
    
    # Only keep PTPN11 chromosome
    chunk = chunk[chunk['chr'] == chrom]
    
    # Keep only positions within PTPN11 range
    filtered_chunk = chunk[
        (chunk['grch38_pos'] >= min_pos) &
        (chunk['grch38_pos'] <= max_pos)
    ]
    
    if not filtered_chunk.empty:
        ptpn11_revel_chunks.append(filtered_chunk)
    
    # Early stop: REVEL is sorted by grch38_pos
    if chunk['grch38_pos'].max() > max_pos:
        break

# Concatenate all filtered chunks
if ptpn11_revel_chunks:
    ptpn11_revel = pd.concat(ptpn11_revel_chunks)
    ptpn11_revel.to_csv( r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL.csv", index=False)


##### BayesDel

Downloaded from https://drive.google.com/drive/folders/1K4LI6ZSsUGBhHoChUtegC8bgCt7hbQlA (2017! version)

Need to install and run VICTOR locally (Linux)


In [74]:
chrom37, min_pos37, max_pos37 = get_chr_range(ClinVar_df, gene, gene_col="Gene(s)", loc_col="GRCh37Location", chrom_col="GRCh37Chromosome")


 Gene: PTPN11
 Chromosome: 12.0
 Position range: 112856917 - 112942558


In [98]:
# Unzipped file path for gene specific chrom and GRCH37 location
bayesdel_noAF_file = r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\BayesDel_170824_noAF\BayesDel_170824_noAF\BayesDel_170824_noAF_chr12\BayesDel_170824_noAF_chr12"

with open(bayesdel_noAF_file, "r") as f:
    for _ in range(10):
        print(f.readline().strip())


#Chr	Start	ref	alt	BayesDel_nsfp33a_noAF
12	176049	A	C	-0.217265
12	176049	A	G	-0.171535
12	176049	A	T	-0.21727
12	176050	T	A	-0.288296
12	176050	T	C	-0.265607
12	176050	T	G	-0.301534
12	176051	G	A	-0.0488746
12	176051	G	C	-0.0488725
12	176051	G	T	-0.048873


In [99]:
def load_bayesdel_region(file_path, min_pos, max_pos, output_csv=None, chunksize=100_000, columns=None):
    chunks = []
    if columns is None:
        columns = ["Chr", "Start", "Ref", "Alt", "Score"]

    for chunk in pd.read_csv(file_path, sep="\t", names=columns, chunksize=chunksize, comment="#"):
        chunk["Start"] = pd.to_numeric(chunk["Start"], errors="coerce")
        # Filter by genomic position
        filtered = chunk[(chunk["Start"] >= min_pos) & (chunk["Start"] <= max_pos)]

        if not filtered.empty:
            chunks.append(filtered)

    if chunks:
        df_region = pd.concat(chunks, ignore_index=True)

    # Save to CSV 
    if output_csv:
        df_region.to_csv(output_csv, index=False)
        
    return df_region





In [100]:
bayesdel_noAF_file = r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\BayesDel_170824_noAF\BayesDel_170824_noAF\BayesDel_170824_noAF_chr12\BayesDel_170824_noAF_chr12"
bayesdel_addAF_file = r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\BayesDel_170824_noAF\BayesDel_170824_noAF\BayesDel_170824_noAF_chr12\BayesDel_170824_noAF_chr12"

# Load noAF region and save output
PTPN11_bayesdel_noAF = load_bayesdel_region(bayesdel_noAF_file, min_pos37, max_pos37, output_csv=r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_BayesDel_noAF.csv")

# Load addAF region and save output
PTPN11_bayesdel_addAF = load_bayesdel_region(bayesdel_addAF_file, min_pos37, max_pos37, output_csv=r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_BayesDel_addAF.csv")

#print("\nnoAF columns:", df_noAF.columns.tolist())
#print("\naddAF columns:", df_addAF.columns.tolist())

#### Merge Revel & BayesDel

In [103]:
print(revel_df["Ensembl_transcriptid"].unique())


['ENST00000392597;ENST00000351677;ENST00000392596' 'ENST00000530818'
 'ENST00000392596' 'ENST00000392597;ENST00000351677' 'ENST00000351677'
 'ENST00000392597']


In [10]:
revel_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL.csv")


In [11]:
revel_df.head()

chr   hg19_pos   grch38_pos ref alt aaref aaalt  REVEL Ensembl_transcriptid
0   12  112856917  112419113.0   T   A     M     K  0.294  ENST00000392597;...
1   12  112856917  112419113.0   T   C     M     T  0.315  ENST00000392597;...
2   12  112856917  112419113.0   T   G     M     R  0.202  ENST00000392597;...
3   12  112856918  112419114.0   G   A     M     I  0.222  ENST00000392597;...
4   12  112856918  112419114.0   G   C     M     I  0.222  ENST00000392597;...

In [12]:
# Load PTPN11_REVEL and BayesDel
revel_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL.csv")
bayesdel_noAF_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_BayesDel_noAF.csv")
bayesdel_addAF_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_BayesDel_addAF.csv")

# Merge PTPN11_REVEL scores ?????on ClinVar
bayesdel_noAF_df = bayesdel_noAF_df.rename(columns={"Score": "BayesDel_noAF"})
bayesdel_addAF_df = bayesdel_addAF_df.rename(columns={"Score": "BayesDel_addAF"})

revel_bayesdel_noAF_df = pd.merge(
    revel_df,
    bayesdel_noAF_df,
    left_on=['hg19_pos', 'ref', 'alt'],
    right_on=['Start', 'Ref', 'Alt'],
    how='left',
)

revel_bayesdel_noAF_df = revel_bayesdel_noAF_df.drop(columns=['Chr','Start', 'Ref', 'Alt'])

revel_bayesdel_df = pd.merge(
    revel_bayesdel_noAF_df,
    bayesdel_addAF_df,
    left_on=['hg19_pos', 'ref', 'alt'],
    right_on=['Start', 'Ref', 'Alt'],
    how='left',
)

revel_bayesdel_df = revel_bayesdel_df.drop(columns=['Chr','Start', 'Ref', 'Alt'])



In [13]:
revel_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL.csv")


In [17]:
revel_df.head(30)

chr   hg19_pos   grch38_pos ref alt aaref aaalt  REVEL  \
0    12  112856917  112419113.0   T   A     M     K  0.294   
1    12  112856917  112419113.0   T   C     M     T  0.315   
2    12  112856917  112419113.0   T   G     M     R  0.202   
3    12  112856918  112419114.0   G   A     M     I  0.222   
4    12  112856918  112419114.0   G   C     M     I  0.222   
5    12  112856918  112419114.0   G   T     M     I  0.222   
6    12  112856919  112419115.0   A   C     T     P  0.194   
7    12  112856919  112419115.0   A   G     T     A  0.054   
8    12  112856919  112419115.0   A   T     T     S  0.048   
9    12  112856920  112419116.0   C   A     T     K  0.155   
10   12  112856920  112419116.0   C   G     T     R  0.063   
11   12  112856920  112419116.0   C   T     T     I  0.213   
12   12  112856922  112419118.0   T   A     S     T  0.363   
13   12  112856922  112419118.0   T   C     S     P  0.647   
14   12  112856922  112419118.0   T   G     S     A  0.303   
15   12  112856923  112419119.0   C   G     S     W  0.710   
16   12  112856923  112419119.0   C   T     S     L  0.630   
17   12  112856925  112419121.0   C   G     R     G  0.518   
18   12  112856925  112419121.0   C   T     R     W  0.771   
19   12  112856926  112419122.0   G   A     R     Q  0.393   
20   12  112856926  112419122.0   G   C     R     P  0.635   
21   12  112856926  112419122.0   G   T     R     L  0.432   
22   12  112856928  112419124.0   A   G     R     G  0.565   
23   12  112856929  112419125.0   G   A     R     K  0.394   
24   12  112856929  112419125.0   G   C     R     T  0.774   
25   12  112856929  112419125.0   G   T     R     I  0.819   
26   12  112884080  112446276.0   A   C     R     S  0.721   
27   12  112884080  112446276.0   A   T     R     S  0.716   
28   12  112884081  112446277.0   T   A     W     R  0.941   
29   12  112884081  112446277.0   T   C     W     R  0.941   

   Ensembl_transcriptid  
0   ENST00000392597;...  
1   ENST00000392597;...  
2   ENST00000392597;...  
3   ENST00000392597;...  
4   ENST00000392597;...  
5   ENST00000392597;...  
6   ENST00000392597;...  
7   ENST00000392597;...  
8   ENST00000392597;...  
9   ENST00000392597;...  
10  ENST00000392597;...  
11  ENST00000392597;...  
12  ENST00000392597;...  
13  ENST00000392597;...  
14  ENST00000392597;...  
15  ENST00000392597;...  
16  ENST00000392597;...  
17  ENST00000392597;...  
18  ENST00000392597;...  
19  ENST00000392597;...  
20  ENST00000392597;...  
21  ENST00000392597;...  
22  ENST00000392597;...  
23  ENST00000392597;...  
24  ENST00000392597;...  
25  ENST00000392597;...  
26  ENST00000392597;...  
27  ENST00000392597;...  
28  ENST00000392597;...  
29  ENST00000392597;...

#### Convert protein to genomic coordinates

In [18]:
# ENST00000635625 ENST00000351677 ENST00000392597

def getPTPN11GC(position, delay = 0.2):
    server = "https://rest.ensembl.org"
    adjusted_position = position + 165
    ext = "/map/cdna/ENST00000351677/"+ str(adjusted_position) + ".." + str(adjusted_position) + "?"
    
    time.sleep(delay)
    r = requests.get(server+ext, headers={ "Content-Type" : "application/json"})
    if not r.ok:
      r.raise_for_status()
      sys.exit()
 
    decoded = r.json()
    return(decoded['mappings'][0]['start'])

In [144]:
NSEuronet_df = extendTableDNA(NSEuronet_df,mutation="cDNA")

In [145]:
NSEuronet_df

Gene                 cDNA      Protein_desc              Disease  \
1     PTPN11             c.922A>G           p.N308D      Noonan syndrome   
2     PTPN11             c.184T>G            p.Y62D      Noonan syndrome   
3     PTPN11             c.922A>G           p.N308D      Noonan syndrome   
4     PTPN11            c.1232C>T           p.T411M      Noonan syndrome   
5     PTPN11            c.1232C>T           p.T411M      Noonan syndrome   
6     PTPN11            c.1232C>T           p.T411M      Noonan syndrome   
7     PTPN11            c.1529A>G           p.Q510R  NF1-Noonan syndrome   
8     PTPN11             c.179G>C            p.G60A      Noonan syndrome   
9     PTPN11             c.182A>G            p.D61G      Noonan syndrome   
10    PTPN11             c.184T>G            p.Y62D      Noonan syndrome   
11    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
12    PTPN11             c.218C>T            p.T73I      Noonan syndrome   
13    PTPN11             c.236A>G            p.Q79R      Noonan syndrome   
14    PTPN11             c.236A>G            p.Q79R      Noonan syndrome   
15    PTPN11             c.236A>G            p.Q79R      Noonan syndrome   
16    PTPN11             c.317A>C           p.D106A      Noonan syndrome   
17    PTPN11             c.417G>C           p.E139D      Noonan syndrome   
18    PTPN11             c.417G>C           p.E139D      Noonan syndrome   
19    PTPN11             c.854T>C           p.F285S      Noonan syndrome   
20    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
21    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
22    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
23    PTPN11            c.1472C>A           p.P491H      Noonan syndrome   
24    PTPN11            c.1471C>T           p.P491S      Noonan syndrome   
25    PTPN11            c.1510A>G           p.M504V      Noonan syndrome   
26    PTPN11            c.1505C>T           p.S502L      Noonan syndrome   
27    PTPN11             c.836A>G           p.Y279C  LEOPARD syndrome...   
28    PTPN11            c.1472C>T           p.P491L      Noonan syndrome   
29    PTPN11            c.1472C>T           p.P491L      Noonan syndrome   
30    PTPN11            c.1472C>T           p.P491L      Noonan syndrome   
31    PTPN11             c.766C>A           p.Q256K      Noonan syndrome   
32    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
33    PTPN11             c.218C>T            p.T73I      Noonan syndrome   
34    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
35    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
36    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
37    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
38    PTPN11             c.218C>T            p.T73I      Noonan syndrome   
39    PTPN11             c.172A>G            p.N58D      Noonan syndrome   
40    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
41    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
42    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
43    PTPN11             c.206A>T            p.E69V      Noonan syndrome   
44    PTPN11             c.836A>G           p.Y279C      Noonan syndrome   
45    PTPN11             c.844A>G           p.I282V      Noonan syndrome   
46    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
47    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
48    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
49    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
50    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
51    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
52    PTPN11             c.922A>G           p.N308D     

In [146]:
NSEuronet_df["pos"] = NSEuronet_df["codon"].apply(lambda x: getPTPN11GC(int(x)))


In [153]:
NSEuronet_df

Gene                 cDNA      Protein_desc              Disease  \
1     PTPN11             c.922A>G           p.N308D      Noonan syndrome   
2     PTPN11             c.184T>G            p.Y62D      Noonan syndrome   
3     PTPN11             c.922A>G           p.N308D      Noonan syndrome   
4     PTPN11            c.1232C>T           p.T411M      Noonan syndrome   
5     PTPN11            c.1232C>T           p.T411M      Noonan syndrome   
6     PTPN11            c.1232C>T           p.T411M      Noonan syndrome   
7     PTPN11            c.1529A>G           p.Q510R  NF1-Noonan syndrome   
8     PTPN11             c.179G>C            p.G60A      Noonan syndrome   
9     PTPN11             c.182A>G            p.D61G      Noonan syndrome   
10    PTPN11             c.184T>G            p.Y62D      Noonan syndrome   
11    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
12    PTPN11             c.218C>T            p.T73I      Noonan syndrome   
13    PTPN11             c.236A>G            p.Q79R      Noonan syndrome   
14    PTPN11             c.236A>G            p.Q79R      Noonan syndrome   
15    PTPN11             c.236A>G            p.Q79R      Noonan syndrome   
16    PTPN11             c.317A>C           p.D106A      Noonan syndrome   
17    PTPN11             c.417G>C           p.E139D      Noonan syndrome   
18    PTPN11             c.417G>C           p.E139D      Noonan syndrome   
19    PTPN11             c.854T>C           p.F285S      Noonan syndrome   
20    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
21    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
22    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
23    PTPN11            c.1472C>A           p.P491H      Noonan syndrome   
24    PTPN11            c.1471C>T           p.P491S      Noonan syndrome   
25    PTPN11            c.1510A>G           p.M504V      Noonan syndrome   
26    PTPN11            c.1505C>T           p.S502L      Noonan syndrome   
27    PTPN11             c.836A>G           p.Y279C  LEOPARD syndrome...   
28    PTPN11            c.1472C>T           p.P491L      Noonan syndrome   
29    PTPN11            c.1472C>T           p.P491L      Noonan syndrome   
30    PTPN11            c.1472C>T           p.P491L      Noonan syndrome   
31    PTPN11             c.766C>A           p.Q256K      Noonan syndrome   
32    PTPN11             c.923A>G           p.N308S      Noonan syndrome   
33    PTPN11             c.218C>T            p.T73I      Noonan syndrome   
34    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
35    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
36    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
37    PTPN11            c.1403C>T           p.T468M  LEOPARD syndrome...   
38    PTPN11             c.218C>T            p.T73I      Noonan syndrome   
39    PTPN11             c.172A>G            p.N58D      Noonan syndrome   
40    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
41    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
42    PTPN11             c.188A>G            p.Y63C      Noonan syndrome   
43    PTPN11             c.206A>T            p.E69V      Noonan syndrome   
44    PTPN11             c.836A>G           p.Y279C      Noonan syndrome   
45    PTPN11             c.844A>G           p.I282V      Noonan syndrome   
46    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
47    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
48    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
49    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
50    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
51    PTPN11             c.922A>G           p.N308D      Noonan syndrome   
52    PTPN11             c.922A>G           p.N308D     

##### Check with gnomAD and ClinVar

In [135]:
checkgnomAD = extendTableDNA(gnomAD_df,mutation="Transcript Consequence")

In [136]:
checkgnomAD["pos"] = checkgnomAD["codon"].apply(lambda x: getPTPN11GC(int(x)))


In [45]:
checkgnomAD.head()

gnomAD ID  Chromosome   Position        rsIDs Reference Alternate  \
54   12-112419116-C-T          12  112419116  rs267606990         C         T   
58   12-112419121-C-G          12  112419121  rs886041517         C         G   
59   12-112419122-G-A          12  112419122          NaN         G         A   
195  12-112446278-G-T          12  112446278          NaN         G         T   
196  12-112446279-G-T          12  112446279   rs79203122         G         T   

            Source Filters - exomes Filters - genomes         Transcript  \
54   gnomAD Exomes             PASS               NaN  ENST00000351677.7   
58   gnomAD Exomes             PASS               NaN  ENST00000351677.7   
59   gnomAD Exomes             PASS               NaN  ENST00000351677.7   
195  gnomAD Exomes             PASS               NaN  ENST00000351677.7   
196  gnomAD Exomes             PASS               NaN  ENST00000351677.7   

    HGVS Consequence Protein Consequence Transcript Consequence  \
54         p.Thr2Ile           p.Thr2Ile               c.5C>T     
58         p.Arg4Gly           p.Arg4Gly              c.10C>G     
59         p.Arg4Gln           p.Arg4Gln              c.11G>A     
195        p.Trp6Leu           p.Trp6Leu              c.17G>T     
196        p.Trp6Cys           p.Trp6Cys              c.18G>T     

       VEP Annotation ClinVar Germline Classification  ClinVar Variation ID  \
54   missense_variant  Pathogenic/Likel...                         13349.0    
58   missense_variant  Conflicting clas...                        280283.0    
59   missense_variant    Likely pathogenic                       2729546.0    
195  missense_variant                  NaN                             NaN    
196  missense_variant  Uncertain signif...                       2785856.0    

    Flags  Allele Count  Allele Number  Allele Frequency  Homozygote Count  \
54    NaN             4        1528266      2.617345e-06                 0   
58    NaN             2        1526086      1.310542e-06                 0   
59    NaN             1        1523540      6.563661e-07                 0   
195   NaN             1        1613914      6.196117e-07                 0   
196   NaN             3        1613968      1.858773e-06                 0   

     Hemizygote Count Filters - joint GroupMax FAF group  \
54                  0            PASS                nfe   
58                  0            PASS                nfe   
59                  0            PASS                NaN   
195                 0            PASS                NaN   
196                 0            PASS                nfe   

     GroupMax FAF frequency  cadd  revel_max  spliceai_ds_max  \
54          7.000000e-07     31.0      0.213             0.01   
58          2.900000e-07     33.0      0.518             0.05   
59                   NaN     28.4      0.393             0.00   
195                  NaN     32.0      0.897             0.00   
196         2.800000e-07     32.0      0.920             0.00   

     pangolin_largest_ds  phylop  sift_max  polyphen_max  \
54                 -0.02    8.35      0.03         0.068   
58                 -0.05    8.35      0.01         0.289   
59                  0.00    8.25      0.01         0.344   
195                 0.00    6.27      0.00         0.999   
196                -0.01    6.27      0.02         0.987   

     Allele Count African/African American  \
54                     0                     
58                     0                     
59                     0                     
195                    0                     
196                    0                     

     Allele Number African/African American  \
54                 70690                      
58                 70428                      
59                 70172                      
195                75018                      
196                75030                      

     Homozygote Count African/African American  

In [139]:
filteredG = checkgnomAD[checkgnomAD["Position"] != checkgnomAD["pos"]]
#print(filteredG[["Transcript Consequence", "Position", "pos"]])
filteredG

gnomAD ID  Chromosome   Position         rsIDs Reference  \
879   12-112457295-C-A          12  112457295           NaN         C   
880   12-112457299-G-T          12  112457299    rs60920694         G   
881   12-112457304-A-T          12  112457304  rs1050233131         A   
882   12-112457305-T-G          12  112457305   rs945278667         T   
884   12-112457313-A-G          12  112457313  rs1432432570         A   
885   12-112457314-G-C          12  112457314  rs1479284129         G   
1491  12-112486463-G-T          12  112486463   rs779291780         G   
1492  12-112486464-C-T          12  112486464           NaN         C   
1494  12-112486466-C-G          12  112486466   rs377257792         C   
1498  12-112486469-C-T          12  112486469           NaN         C   
2000  12-112504106-G-A          12  112504106  rs1277567841         G   
2001  12-112504107-C-T          12  112504107   rs539607667         C   
2003  12-112504118-C-T          12  112504118  rs1333430231         C   
2005  12-112504140-A-G          12  112504140  rs2038907536         A   
2006  12-112504143-C-T          12  112504143  rs1405559783         C   
2007  12-112504148-T-G          12  112504148  rs1391962729         T   
2009  12-112504162-C-G          12  112504162  rs2038907763         C   
2010  12-112504164-C-T          12  112504164   rs761170169         C   
2011  12-112504167-G-C          12  112504167  rs1356719888         G   
2168  12-112505826-T-C          12  112505826  rs2038928621         T   
2171  12-112505842-C-T          12  112505842   rs730880328         C   
2172  12-112505844-C-G          12  112505844  rs2038928947         C   

     Alternate               Source Filters - exomes Filters - genomes  \
879          A        gnomAD Exomes             PASS               NaN   
880          T  gnomAD Exomes,gn...             PASS              PASS   
881          T  gnomAD Exomes,gn...             PASS              PASS   
882          G       gnomAD Genomes              NaN              PASS   
884          G       gnomAD Genomes              NaN              PASS   
885          C        gnomAD Exomes             PASS               NaN   
1491         T        gnomAD Exomes             PASS               NaN   
1492         T        gnomAD Exomes             PASS               NaN   
1494         G        gnomAD Exomes             PASS               NaN   
1498         T        gnomAD Exomes             PASS               NaN   
2000         A       gnomAD Genomes              NaN              PASS   
2001         T       gnomAD Genomes              NaN              PASS   
2003         T       gnomAD Genomes              NaN              PASS   
2005         G       gnomAD Genomes              NaN              PASS   
2006         T       gnomAD Genomes              NaN              PASS   
2007         G       gnomAD Genomes              NaN              PASS   
2009         G       gnomAD Genomes              NaN              PASS   
2010         T       gnomAD Genomes              NaN              PASS   
2011         C       gnomAD Genomes              NaN              PASS   
2168         C       gnomAD Genomes              NaN              PASS   
2171         T       gnomAD Genomes              NaN              PASS   
2172         G       gnomAD Genomes              NaN              PASS   

             Transcript HGVS Consequence Protein Consequence  \
879   ENST00000530818.1       p.Ala99Asp          p.Ala99Asp   
880   ENST00000530818.1      p.Glu100Asp         p.Glu100Asp   
881   ENST00000530818.1      p.Asp102Val         p.Asp102Val   
882   ENST00000530818.1      p.Asp102Glu         p.Asp102Glu   
884   ENST00000530818.1      p.Gln105Arg         p.Gln105Arg   
885   ENST00000530818.1      p.Gln105His         p.Gln105His   
1491  ENST00000635625.1      p.Ala409Ser         p.Ala409Ser   
1492  ENST00000635625.1      p.Ala409Val         p.Ala409Val   
1494  ENST00000635625.1      p.Leu410Val         p.Leu

In [148]:
unique_consequences = filteredG['Transcript Consequence'].unique()


In [151]:
# Convert NSEuronet cDNA column to a set for faster lookup
cDNA_set = set(NSEuronet_df['cDNA'].dropna())

# Check which unique_consequences are in NSEuronet cDNA
consequences_in_NSEuronet = [cons for cons in unique_consequences if cons in cDNA_set]

print(consequences_in_NSEuronet)

[]


In [64]:
len(ClinVar_df)

557

In [68]:
with pd.option_context('display.max_colwidth', None):
    print(ClinVar_df[ClinVar_df["cDNA_desc"].isna()])

# Though missense, drop for the case of checking genomic coordinate mapping
checkClinVar = ClinVar_df.dropna(subset=["cDNA_desc"])


                                                      Name Gene(s)  \
144     NM_002834.5(PTPN11):c.180_181delinsAA (p.Asp61Asn)  PTPN11   
154     NM_002834.5(PTPN11):c.184_185delinsAT (p.Tyr62Ile)  PTPN11   
160     NM_002834.5(PTPN11):c.188_189delinsGC (p.Tyr63Cys)  PTPN11   
500    NM_002834.5(PTPN11):c.771_772delinsAA (p.Glu258Lys)  PTPN11   
508    NM_002834.5(PTPN11):c.781_782delinsTA (p.Leu261Tyr)  PTPN11   
875  NM_002834.5(PTPN11):c.1402_1403delinsGA (p.Thr468Glu)  PTPN11   
956  NM_002834.5(PTPN11):c.1506_1507delinsCC (p.Gly503Arg)  PTPN11   
967  NM_002834.5(PTPN11):c.1517_1518delinsCC (p.Gln506Pro)  PTPN11   

          Protein change              Condition(s)     Accession  \
144           D61N, D60N              not provided  VCV000372703   
154           Y62I, Y61I                 RASopathy  VCV002814413   
160           Y63C, Y62C              not provided  VCV000372674   
500         E257K, E258K  Cardiovascular phenotype  VCV004147357   
508         L260Y, L261Y     

In [69]:
checkClinVar = extendTableDNA(checkClinVar,mutation="cDNA_desc")

C:\Users\zcemcel\AppData\Local\Temp\ipykernel_6464\359544897.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  table["chr"] = chrom # extracted from ClinVar
C:\Users\zcemcel\AppData\Local\Temp\ipykernel_6464\359544897.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  table["codon"] = table[mutation].apply(lambda x: re.sub("\D+","",x))
C:\Users\zcemcel\AppData\Local\Temp\ipykernel_6464\359544897.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using

In [ ]:
checkClinVar["pos"] = checkClinVar["codon"].apply(lambda x: getPTPN11GC(int(x)))


In [50]:
checkClinVar.head()

NameError: name 'checkClinVar' is not defined

In [124]:
# ENST00000635625

filteredC = checkClinVar[checkClinVar["GRCh38Location"] != checkClinVar["pos"]]
print(filteredC[["Protein_change","cDNA_desc", "GRCh38Location", "pos"]])

     Protein_change  cDNA_desc  GRCh38Location        pos
778           G409A  c.1226G>C       112486476  112486464
780           N410H  c.1228A>C       112486478  112486466
781           T411K  c.1232C>A       112486482  112486470
782           T411M  c.1232C>T       112486482  112486470
784           E412G  c.1235A>G       112486485  112486473
785           T414M  c.1241C>T       112486491  112486479
789           V415F  c.1243G>T       112486493  112486481
791           R421W  c.1261C>T       112486511  112486499
792           R421Q  c.1262G>A       112486512  112486500
796           P424L  c.1271C>T       112486521  112486509
798           H426N  c.1276C>A       112486526  112486514
799           H426P  c.1277A>C       112486527  112486515
802           V428L  c.1282G>C       112486532  112486520
803           V428L  c.1282G>T       112486532  112486520
804           V428M  c.1282G>A       112486532  112486520
805           S430T  c.1289G>C       112486539  112486527
807           

In [118]:
filteredC["pos"].dtype


dtype('int64')

In [134]:
# ENST00000351677 with adjustment 


checkClinVar["GRCh38Location"] = pd.to_numeric(checkClinVar["GRCh38Location"], errors="coerce")
filteredC = checkClinVar[checkClinVar["GRCh38Location"] != checkClinVar["pos"]]
print(filteredC[["Protein_change","cDNA_desc", "GRCh38Location", "pos"]])

Empty DataFrame
Columns: [Protein_change, cDNA_desc, GRCh38Location, pos]
Index: []


C:\Users\zcemcel\AppData\Local\Temp\ipykernel_3456\69585137.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  checkClinVar["GRCh38Location"] = pd.to_numeric(checkClinVar["GRCh38Location"], errors="coerce")


In [138]:
print(checkClinVar[["Protein_change","cDNA_desc", "GRCh38Location", "pos"]])

     Protein_change  cDNA_desc  GRCh38Location        pos
24              M1R     c.2T>G       112419113  112419113
25              T2I     c.5C>T       112419116  112419116
30              R4G    c.10C>G       112419121  112419121
31              R4Q    c.11G>A       112419122  112419122
58              W6C    c.18G>T       112446279  112446279
59              W6C    c.18G>C       112446279  112446279
60             N10Y    c.28A>T       112446289  112446289
61             N10H    c.28A>C       112446289  112446289
62             N10D    c.28A>G       112446289  112446289
63             N10T    c.29A>C       112446290  112446290
64             N10S    c.29A>G       112446290  112446290
65             I11T    c.32T>C       112446293  112446293
66             T12A    c.34A>G       112446295  112446295
69             V14L    c.40G>T       112446301  112446301
72             N18D    c.52A>G       112446313  112446313
73             N18S    c.53A>G       112446314  112446314
75            

#### Convert genomic coordinates to protein positions

In [44]:
print(revel_bayesdel_df[revel_bayesdel_df.isna().any(axis=1)])


Empty DataFrame
Columns: [chr, hg19_pos, grch38_pos, ref, alt, aaref, aaalt, REVEL, Ensembl_transcriptid, BayesDel_noAF, BayesDel_addAF]
Index: []


In [43]:
# Filter out suspect transcript IDs
revel_bayesdel_df = revel_bayesdel_df[revel_bayesdel_df['Ensembl_transcriptid'].str.contains("ENST00000392597|ENST00000351677", na=False)]


In [47]:
def annotatePP(df, transcript_id="ENST00000351677", batch_size=200, delay=0.2):
    server = "https://rest.ensembl.org"
    ext = "/vep/human/region"
    headers = {"Content-Type": "application/json", "Accept": "application/json"}

    protein_positions = [None] * len(df)  # pre-allocate list

    # Split dataframe into batches
    for start in range(0, len(df), batch_size):
        batch = df.iloc[start:start+batch_size]
        variants = [
            f"{row['chr']} {int(row['grch38_pos'])} {int(row['grch38_pos'])} {row['ref']}/{row['alt']}"
            for idx, row in batch.iterrows()
        ]
        payload = {"variants": variants}
        if transcript_id:
            payload["transcript_id"] = transcript_id

        try:
            time.sleep(delay)
            r = requests.post(server + ext, headers=headers, json=payload)
            r.raise_for_status()
            decoded = r.json()
        except Exception as e:
            print(f"Error querying VEP batch {start}-{start+batch_size}: {e}")
            continue

        # Extract protein positions for each variant in the batch
        for i, result in enumerate(decoded):
            consequences = result.get("transcript_consequences", [])
            protein_pos = None
            if transcript_id:
                for t in consequences:
                    if t["transcript_id"] == transcript_id:
                        protein_pos = t.get("protein_start")
                        break
            elif consequences:
                protein_pos = consequences[0].get("protein_start")
            protein_positions[start + i] = protein_pos

    df['protein_pos'] = protein_positions
    return df


In [48]:
revel_bayesdel_df = annotatePP(revel_bayesdel_df)


In [82]:
revel_bayesdel_df.head()

chr   hg19_pos  grch38_pos ref alt aaref aaalt  REVEL Ensembl_transcriptid  \
0   12  112856917   112419113   T   A     M     K  0.294  ENST00000392597;...   
1   12  112856917   112419113   T   C     M     T  0.315  ENST00000392597;...   
2   12  112856917   112419113   T   G     M     R  0.202  ENST00000392597;...   
3   12  112856918   112419114   G   A     M     I  0.222  ENST00000392597;...   
4   12  112856918   112419114   G   C     M     I  0.222  ENST00000392597;...   

   BayesDel_noAF  BayesDel_addAF  protein_pos  
0           0.66            0.66          1.0  
1           0.66            0.66          1.0  
2           0.66            0.66          1.0  
3           0.66            0.66          1.0  
4           0.66            0.66          1.0

In [92]:
revel_bayesdel_df.to_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL_BayesDel.csv", index=False)


In [93]:
revel_bayesdel_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL_BayesDel.csv")
revel_bayesdel_df.head()

chr   hg19_pos  grch38_pos ref alt aaref aaalt  REVEL Ensembl_transcriptid  \
0   12  112856917   112419113   T   A     M     K  0.294  ENST00000392597;...   
1   12  112856917   112419113   T   C     M     T  0.315  ENST00000392597;...   
2   12  112856917   112419113   T   G     M     R  0.202  ENST00000392597;...   
3   12  112856918   112419114   G   A     M     I  0.222  ENST00000392597;...   
4   12  112856918   112419114   G   C     M     I  0.222  ENST00000392597;...   

   BayesDel_noAF  BayesDel_addAF  protein_pos  
0           0.66            0.66          1.0  
1           0.66            0.66          1.0  
2           0.66            0.66          1.0  
3           0.66            0.66          1.0  
4           0.66            0.66          1.0

In [70]:
checkClinVar.head()

Name Gene(s) Protein change         Condition(s)  \
24  NM_002834.5(PTPN...  PTPN11            M1R  Juvenile myelomo...   
25  NM_002834.5(PTPN...  PTPN11            T2I  LEOPARD syndrome...   
30  NM_002834.5(PTPN...  PTPN11            R4G         not provided   
31  NM_002834.5(PTPN...  PTPN11            R4Q            RASopathy   
58  NM_002834.5(PTPN...  PTPN11            W6C  Cardiovascular p...   

       Accession  GRCh37Chromosome GRCh37Location  GRCh38Chromosome  \
24  VCV003574257              12.0      112856917              12.0   
25  VCV000013349              12.0      112856920              12.0   
30  VCV000280283              12.0      112856925              12.0   
31  VCV002729546              12.0      112856926              12.0   
58  VCV002785856              12.0      112884083              12.0   

   GRCh38Location  VariationID  AlleleID(s)      dbSNP ID  \
24      112419113      3574257      3707172           NaN   
25      112419116        13349        28388   rs267606990   
30      112419121       280283       264573   rs886041517   
31      112419122      2729546      2893458  rs2499756229   
58      112446279      2785856      2941818    rs79203122   

         Canonical SPDI         Variant type Molecular consequence  \
24  NC_000012.12:112...  single nucleotid...  missense variant...    
25  NC_000012.12:112...  single nucleotid...     missense variant    
30  NC_000012.12:112...  single nucleotid...     missense variant    
31  NC_000012.12:112...  single nucleotid...     missense variant    
58  NC_000012.12:112...  single nucleotid...     missense variant    

   Germline classification Germline date last evaluated  \
24    Likely pathogenic            Jun 20, 2024           
25  Pathogenic/Likel...            May 29, 2025           
30  Conflicting clas...             Nov 8, 2024           
31    Likely pathogenic             Dec 3, 2024           
58  Uncertain signif...             Jan 2, 2025           

   Germline review status  Somatic clinical impact  \
24  criteria provide...                    NaN       
25  criteria provide...                    NaN       
30  criteria provide...                    NaN       
31  criteria provide...                    NaN       
58  criteria provide...                    NaN       

    Somatic clinical impact date last evaluated  \
24                  NaN                           
25                  NaN                           
30                  NaN                           
31                  NaN                           
58                  NaN                           

    Somatic clinical impact review status Oncogenicity classification  \
24                  NaN                                    NaN          
25                  NaN                                    NaN          
30                  NaN                                    NaN          
31                  NaN                                    NaN          
58                  NaN                                    NaN          

   Oncogenicity date last evaluated Oncogenicity review status  Unnamed: 24  \
24                  NaN                              NaN                NaN   
25                  NaN                              NaN                NaN   
30                  NaN                              NaN                NaN   
31                  NaN                              NaN                NaN   
58                  NaN                              NaN                NaN   

   Protein_desc cDNA_desc Protein_change  AApos AAfrom AAto  DCharge  \
24    p.Met1Arg    c.2T>G            M1R      1      M    R        1   
25    p.Thr2Ile    c.5C>T            T2I      2      T    I        0   
30    p.Arg4Gly   c.10C>G            R4G      4      R    G       -1   
31    p.Arg4Gln   c.11G>A            R4Q      4      R    Q       -1   
58    p.Trp6Cys   c.18G>T            W6C      6      W    C        0   

    DChargeHP  chr codon ref alt  
24      

In [76]:
def annotatePP_2(df, transcript_id="ENST00000351677", batch_size=200, delay=0.2):
    server = "https://rest.ensembl.org"
    ext = "/vep/human/region"
    headers = {"Content-Type": "application/json", "Accept": "application/json"}

    protein_positions = [None] * len(df)  # pre-allocate list

    # Split dataframe into batches
    for start in range(0, len(df), batch_size):
        batch = df.iloc[start:start+batch_size]
        variants = [
            f"{int(row['GRCh38Chromosome'])} {int(row['GRCh38Location'])} {int(row['GRCh38Location'])} {row['ref']}/{row['alt']}"
            for idx, row in batch.iterrows()
        ]
        payload = {"variants": variants}
        if transcript_id:
            payload["transcript_id"] = transcript_id

        try:
            time.sleep(delay)
            r = requests.post(server + ext, headers=headers, json=payload)
            r.raise_for_status()
            decoded = r.json()
        except Exception as e:
            print(f"Error querying VEP batch {start}-{start+batch_size}: {e}")
            continue

        # Extract protein positions for each variant in the batch
        for i, result in enumerate(decoded):
            consequences = result.get("transcript_consequences", [])
            protein_pos = None
            if transcript_id:
                for t in consequences:
                    if t["transcript_id"] == transcript_id:
                        protein_pos = t.get("protein_start")
                        break
            elif consequences:
                protein_pos = consequences[0].get("protein_start")
            protein_positions[start + i] = protein_pos

    df['protein_pos'] = protein_positions
    return df


In [77]:
checkClinVar = annotatePP_2(checkClinVar)


C:\Users\zcemcel\AppData\Local\Temp\ipykernel_6464\946810774.py:41: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['protein_pos'] = protein_positions


In [80]:
filteredC_2 = checkClinVar[checkClinVar["AApos"] != checkClinVar["protein_pos"]]


In [81]:
filteredC_2

Empty DataFrame
Columns: [Name, Gene(s), Protein change, Condition(s), Accession, GRCh37Chromosome, GRCh37Location, GRCh38Chromosome, GRCh38Location, VariationID, AlleleID(s), dbSNP ID, Canonical SPDI, Variant type, Molecular consequence, Germline classification, Germline date last evaluated, Germline review status, Somatic clinical impact, Somatic clinical impact date last evaluated, Somatic clinical impact review status, Oncogenicity classification, Oncogenicity date last evaluated, Oncogenicity review status, Unnamed: 24, Protein_desc, cDNA_desc, Protein_change, AApos, AAfrom, AAto, DCharge, DChargeHP, chr, codon, ref, alt, protein_pos]
Index: []

### Create datasets

#### Meta-predictor analysis

In [169]:
revel_bayesdel_df_agg["grch38_pos"].dtype

dtype('int64')

In [23]:
# Load PTPN11_REVEL_BayesDel
revel_bayesdel_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL_BayesDel.csv")

# Take aggregate REVEL and BayesDel for multiple SNVs
revel_bayesdel_df['grch38_pos'] = pd.to_numeric(revel_bayesdel_df['grch38_pos'], errors='coerce').astype('Int64')
#revel_bayesdel_df_agg = revel_bayesdel_df.groupby(['aaref','aaalt','protein_pos'], as_index=False)[['REVEL','BayesDel_noAF','BayesDel_addAF']].mean()
revel_bayesdel_df_agg = (
    revel_bayesdel_df
        .groupby(['aaref', 'aaalt', 'protein_pos'], as_index=False)[
            ['REVEL', 'BayesDel_noAF', 'BayesDel_addAF']].mean()
        .rename(columns={
            'aaref': 'AAfrom',
            'aaalt': 'AAto',
            'protein_pos': 'AApos'
        })
)


revel_bayesdel_df_agg.to_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL_BayesDel_agg.csv", index=False)


In [ ]:
"""NEED TO UPDATE THIS AS COLUMNS RENAMED AND ALS CHECK IF SHOULD MERGE ON AAPOS INSTEAD"""

# Merge mean scores on ClinVar
revel_bayesdel_df_agg['grch38_pos'] =revel_bayesdel_df_agg['grch38_pos'].astype(str)
df_stat_long = pd.merge(
    ClinVar_df,
    revel_bayesdel_df_agg,
    left_on=['GRCh38Location', 'AAfrom', 'AAto'], 
    right_on=['grch38_pos', 'aaref', 'aaalt'],
    how='left'  # keep all extended ClinVar missense columns
)

In [174]:
len(df_stat_long)

557

In [181]:
df_stat[df_stat.isna().any(axis=1)]


Empty DataFrame
Columns: [GRCh38Location, GRCh37Location, Protein_change, Germline classification, REVEL, BayesDel_noAF, BayesDel_addAF, AAfrom, AAto, AApos]
Index: []

In [177]:
# Clean df_stat for analysis
#df_stat = df_stat.dropna(subset=['REVEL', 'Germline classification']) # Keep only rows where REVEL or ClinVar classification is not NaN
#df_stat['REVEL'] = pd.to_numeric(df_stat['REVEL'], errors='coerce') # Make sure REVEL is numeric
#df_stat['Germline classification'] = df_stat['Germline classification'].astype(str).str.strip()

# Select only the columns needed for statistical classification
columns_to_keep = [
    'GRCh38Location',
    'GRCh37Location',
    'Protein_change',
    'Germline classification',
    'REVEL',
    'BayesDel_noAF',
    'BayesDel_addAF',
    'AAfrom',
    'AAto',
    'AApos'
]

df_stat = df_stat_long[columns_to_keep]

# Quick check
print(df_stat.head())

  GRCh38Location GRCh37Location Protein_change Germline classification  REVEL  \
0      112419113      112856917            M1R    Likely pathogenic     0.202   
1      112419116      112856920            T2I  Pathogenic/Likel...     0.213   
2      112419121      112856925            R4G  Conflicting clas...     0.518   
3      112419122      112856926            R4Q    Likely pathogenic     0.393   
4      112446279      112884083            W6C  Uncertain signif...     0.920   

   BayesDel_noAF  BayesDel_addAF AAfrom AAto  AApos  
0       0.660000        0.660000      M    R      1  
1       0.010807        0.010807      T    I      2  
2       0.044882        0.044882      R    G      4  
3      -0.022043       -0.022043      R    Q      4  
4       0.512606        0.512606      W    C      6  


In [180]:
df_stat = df_stat.dropna()

In [182]:
# Save merged file
df_stat.to_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_ClinVar_REVEL_BayesDel.csv", index=False)


##### For validating meta predictors with NSEuronet

In [20]:
""" FDONE THIS ABOVE ALREADY
# Load PTPN11_REVEL_BayesDel
revel_bayesdel_df = pd.read_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_REVEL_BayesDel.csv")

# Take aggregate REVEL and BayesDel for multiple SNVs
revel_bayesdel_df_agg = revel_bayesdel_df.groupby(['grch38_pos','protein_pos','aaref','aaalt','Ensembl_transcriptid'], as_index=False)[['REVEL','BayesDel_noAF','BayesDel_addAF']].mean()

"""

In [21]:
len(revel_bayesdel_df_agg)


3569

In [161]:

# Merge mean scores on NSEuronet
df_statNSEuronet = pd.merge(
    NSEuronet_df,
    revel_bayesdel_df_agg,
    left_on=['pos', 'AAfrom', 'AAto'],
    right_on=['grch38_pos', 'aaref', 'aaalt'],
    how='left'  # keep all extended ClinVar missense columns
)


In [162]:
# Save 
df_statNSEuronet.to_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_NSEuronet_REVEL_BayesDel.csv", index=False)


##### For density of meta predictors across gnomAD variants

In [40]:
# Merge mean scores on ClinVar
df_statgnomAD = pd.merge(
    gnomAD_df,
    revel_bayesdel_df_agg,
    left_on=['Position', 'AAfrom', 'AAto'],
    right_on=['grch38_pos', 'aaref', 'aaalt'],
    how='left'  # keep all extended ClinVar missense columns
)

In [41]:
df_statgnomAD.head()

gnomAD ID  Chromosome   Position        rsIDs Reference Alternate  \
0  12-112419116-C-T          12  112419116  rs267606990         C         T   
1  12-112419121-C-G          12  112419121  rs886041517         C         G   
2  12-112419122-G-A          12  112419122          NaN         G         A   
3  12-112446278-G-T          12  112446278          NaN         G         T   
4  12-112446279-G-T          12  112446279   rs79203122         G         T   

          Source Filters - exomes Filters - genomes         Transcript  \
0  gnomAD Exomes             PASS               NaN  ENST00000351677.7   
1  gnomAD Exomes             PASS               NaN  ENST00000351677.7   
2  gnomAD Exomes             PASS               NaN  ENST00000351677.7   
3  gnomAD Exomes             PASS               NaN  ENST00000351677.7   
4  gnomAD Exomes             PASS               NaN  ENST00000351677.7   

  HGVS Consequence Protein Consequence Transcript Consequence  \
0        p.Thr2Ile           p.Thr2Ile               c.5C>T     
1        p.Arg4Gly           p.Arg4Gly              c.10C>G     
2        p.Arg4Gln           p.Arg4Gln              c.11G>A     
3        p.Trp6Leu           p.Trp6Leu              c.17G>T     
4        p.Trp6Cys           p.Trp6Cys              c.18G>T     

     VEP Annotation ClinVar Germline Classification  ClinVar Variation ID  \
0  missense_variant  Pathogenic/Likel...                         13349.0    
1  missense_variant  Conflicting clas...                        280283.0    
2  missense_variant    Likely pathogenic                       2729546.0    
3  missense_variant                  NaN                             NaN    
4  missense_variant  Uncertain signif...                       2785856.0    

  Flags  Allele Count  Allele Number  Allele Frequency  Homozygote Count  \
0   NaN             4        1528266      2.617345e-06                 0   
1   NaN             2        1526086      1.310542e-06                 0   
2   NaN             1        1523540      6.563661e-07                 0   
3   NaN             1        1613914      6.196117e-07                 0   
4   NaN             3        1613968      1.858773e-06                 0   

   Hemizygote Count Filters - joint GroupMax FAF group  \
0                 0            PASS                nfe   
1                 0            PASS                nfe   
2                 0            PASS                NaN   
3                 0            PASS                NaN   
4                 0            PASS                nfe   

   GroupMax FAF frequency  cadd  revel_max  spliceai_ds_max  \
0         7.000000e-07     31.0      0.213             0.01   
1         2.900000e-07     33.0      0.518             0.05   
2                  NaN     28.4      0.393             0.00   
3                  NaN     32.0      0.897             0.00   
4         2.800000e-07     32.0      0.920             0.00   

   pangolin_largest_ds  phylop  sift_max  polyphen_max  \
0                -0.02    8.35      0.03         0.068   
1                -0.05    8.35      0.01         0.289   
2                 0.00    8.25      0.01         0.344   
3                 0.00    6.27      0.00         0.999   
4                -0.01    6.27      0.02         0.987   

   Allele Count African/African American  \
0                    0                     
1                    0                     
2                    0                     
3                    0                     
4                    0                     

   Allele Number African/African American  \
0                70690                      
1                70428                      
2                70172                      
3                75018                      
4                75030                      

   Homozygote Count African/African American  \
0                    0                         
1                    0                         
2                    0

In [42]:
# Save 
df_statgnomAD.to_csv(r"\\rdp.arc.ucl.ac.uk\ritd-ag-project-rd025c-bhall50\ModellingRASopathies RDSS\PTPN11_gnomAD_REVEL_BayesDel.csv", index=False)
